# rf108_plotbinning
Basic functionality: plotting unbinned data with alternate and variable binnings




**Author:** Wouter Verkerke  
<i><small>This notebook tutorial was automatically generated with <a href= "https://github.com/root-project/root/blob/master/documentation/doxygen/converttonotebook.py">ROOTBOOK-izer</a> from the macro found in the ROOT repository  on Wednesday, April 17, 2024 at 11:17 AM.</small></i>

In [1]:
%%cpp -d
#include "RooRealVar.h"
#include "RooDataSet.h"
#include "RooGaussModel.h"
#include "RooDecay.h"
#include "RooBMixDecay.h"
#include "RooCategory.h"
#include "RooBinning.h"
#include "RooPlot.h"
#include "TCanvas.h"
#include "TAxis.h"
#include "TH1.h"
using namespace RooFit;

Setup model
---------------------

Build a B decay pdf with mixing

In [2]:
RooRealVar dt("dt", "dt", -20, 20);
RooRealVar dm("dm", "dm", 0.472);
RooRealVar tau("tau", "tau", 1.547);
RooRealVar w("w", "mistag rate", 0.1);
RooRealVar dw("dw", "delta mistag rate", 0.);

RooCategory mixState("mixState", "B0/B0bar mixing state");
mixState.defineType("mixed", -1);
mixState.defineType("unmixed", 1);
RooCategory tagFlav("tagFlav", "Flavour of the tagged B0");
tagFlav.defineType("B0", 1);
tagFlav.defineType("B0bar", -1);

Build a gaussian resolution model

In [3]:
RooRealVar bias1("bias1", "bias1", 0);
RooRealVar sigma1("sigma1", "sigma1", 0.1);
RooGaussModel gm1("gm1", "gauss model 1", dt, bias1, sigma1);

Construct Bdecay (x) gauss

In [4]:
RooBMixDecay bmix("bmix", "decay", dt, mixState, tagFlav, tau, dm, w, dw, gm1, RooBMixDecay::DoubleSided);

Sample data from model
--------------------------------------------

Sample 2000 events in (dt,mixState,tagFlav) from bmix

In [5]:
std::unique_ptr<RooDataSet> data{bmix.generate(RooArgSet(dt, mixState, tagFlav), 2000)};

input_line_57:2:2: warning: 'data' shadows a declaration with the same name in the 'std' namespace; use '::data' to reference this declaration
 std::unique_ptr<RooDataSet> data{bmix.generate(RooArgSet(dt, mixState, tagFlav), 2000)};
 ^


Show dt distribution with custom binning
-------------------------------------------------------------------------------

Make plot of dt distribution of data in range (-15,15) with fine binning for dt>0 and coarse binning for dt<0

Create binning object with range (-15,15)

In [6]:
RooBinning tbins(-15, 15);

Add 60 bins with uniform spacing in range (-15,0)

In [7]:
tbins.addUniform(60, -15, 0);

Add 15 bins with uniform spacing in range (0,15)

In [8]:
tbins.addUniform(15, 0, 15);

Make plot with specified binning

In [9]:
RooPlot *dtframe = dt.frame(Range(-15, 15), Title("dt distribution with custom binning"));
data->plotOn(dtframe, Binning(tbins));
bmix.plotOn(dtframe);

input_line_61:3:1: error: reference to 'data' is ambiguous
data->plotOn(dtframe, Binning(tbins));
^
input_line_57:2:30: note: candidate found by name lookup is 'data'
 std::unique_ptr<RooDataSet> data{bmix.generate(RooArgSet(dt, mixState, tagFlav), 2000)};
                             ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^


NB: Note that bin density for each bin is adjusted to that of default frame binning as shown
in Y axis label (100 bins --> Events/0.4*Xaxis-dim) so that all bins represent a consistent density distribution

Show mixstate asymmetry with custom binning
------------------------------------------------------------------------------------

Make plot of dt distribution of data asymmetry in 'mixState' with variable binning

Create binning object with range (-10,10)

In [10]:
RooBinning abins(-10, 10);

Add boundaries at 0, (-1,1), (-2,2), (-3,3), (-4,4) and (-6,6)

In [11]:
abins.addBoundary(0);
abins.addBoundaryPair(1);
abins.addBoundaryPair(2);
abins.addBoundaryPair(3);
abins.addBoundaryPair(4);
abins.addBoundaryPair(6);

Create plot frame in dt

In [12]:
RooPlot *aframe = dt.frame(Range(-10, 10), Title("mixState asymmetry distribution with custom binning"));

Plot mixState asymmetry of data with specified custom binning

In [13]:
data->plotOn(aframe, Asymmetry(mixState), Binning(abins));

input_line_65:2:2: error: reference to 'data' is ambiguous
 data->plotOn(aframe, Asymmetry(mixState), Binning(abins));
 ^
input_line_57:2:30: note: candidate found by name lookup is 'data'
 std::unique_ptr<RooDataSet> data{bmix.generate(RooArgSet(dt, mixState, tagFlav), 2000)};
                             ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^


Plot corresponding property of pdf

In [14]:
bmix.plotOn(aframe, Asymmetry(mixState));

Adjust vertical range of plot to sensible values for an asymmetry

In [15]:
aframe->SetMinimum(-1.1);
aframe->SetMaximum(1.1);

NB: For asymmetry distributions no density corrects are needed (and are thus not applied)

Draw plots on canvas

In [16]:
TCanvas *c = new TCanvas("rf108_plotbinning", "rf108_plotbinning", 800, 400);
c->Divide(2);
c->cd(1);
gPad->SetLeftMargin(0.15);
dtframe->GetYaxis()->SetTitleOffset(1.6);
dtframe->Draw();
c->cd(2);
gPad->SetLeftMargin(0.15);
aframe->GetYaxis()->SetTitleOffset(1.6);
aframe->Draw();

input_line_72:2:3: error: use of undeclared identifier 'dtframe'
 (dtframe->GetYaxis()->SetTitleOffset(1.6000000000000001))
  ^
Error in <HandleInterpreterException>: Error evaluating expression (dtframe->GetYaxis()->SetTitleOffset(1.6000000000000001))
Execution of your code was aborted.


Draw all canvases 

In [17]:
%jsroot on
gROOT->GetListOfCanvases()->Draw()